<h1>SAFE LOCATIONS</h1>

HELPS YOU TO HAVE A PLESANT STAY IN THE CITY OF "THE CITY"

In [1]:
#importing Libraries
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import requests
from bs4 import BeautifulSoup
import folium
import json
from sklearn.cluster import KMeans

In [2]:
df_sfcrime = pd.read_csv("https://cocl.us/sanfran_crime_dataset") #importing the dataset for San Fran crime

In [3]:
#cleaning the data
df_sf = df_sfcrime.groupby(['PdDistrict']).count().reset_index()
df_sf.drop(['Category','Descript','DayOfWeek','Date','Time', 'Resolution','Address','X','Y','Location','PdId'], axis=1, inplace=True)
df_sf.rename(columns={'PdDistrict':'Neighborhood', 'IncidntNum':'Count'}, inplace=True)

In [4]:
df_sf #final data

Neighborhood  Count
0      BAYVIEW  14303
1      CENTRAL  17666
2    INGLESIDE  11594
3      MISSION  19503
4     NORTHERN  20100
5         PARK   8699
6     RICHMOND   8922
7     SOUTHERN  28445
8      TARAVAL  11325
9   TENDERLOIN   9942

In [5]:
df_sf=pd.read_csv('export_dataframe1.csv')

In [6]:
gjson = requests.get('https://cocl.us/sanfran_geojson/sanfran_geo.json').json() #geojson for boundries

In [7]:
# create a plain San Francisco map
sf_map = folium.Map(location=[37.773972, -122.431297], zoom_start=13)
sf_map.choropleth(
    geo_data=gjson,
    data=df_sf,
    columns=['Neighborhood','Count'],
    key_on='feature.properties.DISTRICT',
    fill_color='YlOrRd', 
    fill_opacity=0.7, 
    line_opacity=0.2,
    legend_name='San Francisco Crimes'
)

# display map
sf_map

c:\users\aditya\appdata\local\programs\python\python37-32\lib\site-packages\folium\folium.py:415: FutureWarning: The choropleth  method has been deprecated. Instead use the new Choropleth class, which has the same arguments. See the example notebook 'GeoJSON_and_choropleth' for how to do this.
  FutureWarning


In [8]:
CLIENT_ID = 'O2WPUSFNK52W5FYY0MWAWX2MJFE5W0MCLRAXSR0ASAMWUCVN' # your Foursquare ID
CLIENT_SECRET = 'DF4RKL21ALM1K2DYVXCDUBAELSHHANEPE2JCXHDQ5ESH0GGU' # your Foursquare Secret
VERSION = '20200419' # Foursquare API version
LIMIT=1200
RADIUS=1500
print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: O2WPUSFNK52W5FYY0MWAWX2MJFE5W0MCLRAXSR0ASAMWUCVN
CLIENT_SECRET:DF4RKL21ALM1K2DYVXCDUBAELSHHANEPE2JCXHDQ5ESH0GGU


In [9]:
#Provides hotel reccomendation 
url = 'https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&ll={},{},&query=hotels&v=20200419&limit={}&radius={}'.format(
    CLIENT_ID,
    CLIENT_SECRET,
    37.773972,
    -122.431297,
    LIMIT,
    RADIUS)

In [10]:
result = requests.get(url).json()  #requesting the json file
result

{'meta': {'code': 200, 'requestId': '5e9c87186001fe001cfb41d8'},
 'response': {'suggestedFilters': {'header': 'Tap to show:',
   'filters': [{'name': 'Open now', 'key': 'openNow'}]},
  'headerLocation': 'Lower Haight',
  'headerFullLocation': 'Lower Haight, San Francisco',
  'headerLocationGranularity': 'neighborhood',
  'query': 'hotels',
  'totalResults': 44,
  'suggestedBounds': {'ne': {'lat': 37.787472013500015,
    'lng': -122.41424963315906},
   'sw': {'lat': 37.76047198649999, 'lng': -122.44834436684094}},
  'groups': [{'type': 'Recommended Places',
    'name': 'recommended',
    'items': [{'reasons': {'count': 0,
       'items': [{'summary': 'This spot is popular',
         'type': 'general',
         'reasonName': 'globalInteractionReason'}]},
      'venue': {'id': '4bcce0e01dd3eee10f849a3d',
       'name': 'The Grove Inn San Francisco',
       'location': {'address': '890 Grove St San Francisco CA 94117 USA',
        'lat': 37.776971,
        'lng': -122.431242,
        'labe

In [11]:
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

In [12]:
#this is for cleaning up the data in multiple ways
hos = result['response']['groups'][0]['items']
    
hotels = pd.io.json.json_normalize(hos) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
hotels =hotels.loc[:, filtered_columns]

# filter the category for each row
hotels['venue.categories'] = hotels.apply(get_category_type, axis=1)

# clean columns
hotels.columns = [col.split(".")[-1] for col in hotels.columns]

hotels.drop(index=[15,18,38,39,42,43],inplace=True)

c:\users\aditya\appdata\local\programs\python\python37-32\lib\site-packages\ipykernel_launcher.py:4: FutureWarning: pandas.io.json.json_normalize is deprecated, use pandas.json_normalize instead
  after removing the cwd from sys.path.


In [13]:
hotels.reset_index(drop=True,inplace=True)
hotels

name       categories        lat         lng
0        The Grove Inn San Francisco            Hotel  37.776971 -122.431242
1                 Parker Guest House            Hotel  37.762466 -122.428779
2                       1906 Mission            Hotel  37.766546 -122.419969
3                       Hotel Kabuki            Hotel  37.785491 -122.428632
4                           Days Inn            Hotel  37.777504 -122.423897
5                    Casa Loma Hotel            Hotel  37.774975 -122.431012
6             Kimpton Buchanan Hotel            Hotel  37.786697 -122.430329
7                    The Metro Hotel            Hotel  37.772487 -122.437437
8      Edwardian San Francisco Hotel            Hotel  37.773455 -122.421594
9                   Inn at the Opera            Hotel  37.778657 -122.422312
10                Beck's Motor Lodge            Motel  37.765595 -122.431808
11                     Inn on Castro  Bed & Breakfast  37.763436 -122.435022
12                   The Willows Inn  Bed & Breakfast  37.767829 -122.429213
13                          535 Page            Hotel  37.773199 -122.429518
14                     The Parsonage            Hotel  37.772962 -122.425440
15                            Sonder            Hotel  37.774614 -122.422703
16                   Perramont Hotel            Hotel  37.766837 -122.430391
17             Red Coach Motor Lodge            Hotel  37.783281 -122.419377
18                         Oasis Inn            Hotel  37.782940 -122.422121
19                         Oak Hotel            Hotel  37.775953 -122.420759
20  Fairmont San Francisco Penthouse            Hotel  37.769807 -122.420001
21                  The Murphy Suite            Hotel  37.763615 -122.427010
22                     Hotel Sunrise            Hotel  37.765849 -122.421672
23                  Twin Peaks Hotel            Hotel  37.766889 -122.430409
24                   Hotel Mirabelle            Hotel  37.766459 -122.420051
25                   The Sentient Sf            Hotel  37.765408 -122.420799
26                     Kailash Hotel            Hotel  37.765403 -122.420706
27                        Hotel Eula            Hotel  37.764757 -122.420916
28        Best Western Red Coach Inn            Hotel  37.783322 -122.419664
29                      Hotel Potter            Hotel  37.776547 -122.414681
30                     Embassy Hotel            Hotel  37.782320 -122.418938
31             Travelodge by Wyndham            Hotel  37.772071 -122.422249
32                The Chateau Tivoli  Bed & Breakfast  37.779045 -122.433586
33                  Sleep Over Sauce  Bed & Breakfast  37.774601 -122.422617
34                  Hayes Valley Inn  Bed & Breakfast  37.777064 -122.423148
35                       Rodeway Inn            Motel  37.776234 -122.414491
36                       The Rookery       Hotel Pool  37.778529 -122.434232
37          Rodeway Inn Civic Center            Motel  37.782916 -122.421961

In [14]:
hotels.shape

(38, 4)

In [15]:
#adding the hotels to the map
for lat, lng, label in zip(hotels.lat, hotels.lng, hotels.name):
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        color='blue',
        popup=label,
        fill = True,
        fill_color='blue',
        fill_opacity=0.6
    ).add_to(sf_map)
sf_map

In [16]:
#funtion to get nearby venues to the hotels
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [17]:
sf_venues = getNearbyVenues(names=df_sf['Neighborhood'],
                                   latitudes=df_sf['lat'],
                                   longitudes=df_sf['lng']
                                  )

BAYVIEW
CENTRAL
INGLESIDE
MISSION
NORTHERN
PARK
RICHMOND
SOUTHERN
TARAVAL
TENDERLOIN


In [18]:
sf_venues.groupby('Neighborhood').count()

Neighborhood Latitude  Neighborhood Longitude  Venue  \
Neighborhood                                                         
BAYVIEW                           2                       2      2   
CENTRAL                          27                      27     27   
INGLESIDE                        21                      21     21   
MISSION                          66                      66     66   
NORTHERN                         27                      27     27   
PARK                             69                      69     69   
RICHMOND                        100                     100    100   
SOUTHERN                         80                      80     80   
TARAVAL                          36                      36     36   
TENDERLOIN                      100                     100    100   

              Venue Latitude  Venue Longitude  Venue Category  
Neighborhood                                                   
BAYVIEW                    2                2               2  
CENTRAL                   27               27              27  
INGLESIDE                 21               21              21  
MISSION                   66               66              66  
NORTHERN                  27               27              27  
PARK                      69               69              69  
RICHMOND                 100              100             100  
SOUTHERN                  80               80              80  
TARAVAL                   36               36              36  
TENDERLOIN               100              100             100

In [19]:
print('There are {} uniques categories.'.format(len(sf_venues['Venue Category'].unique())))

There are 176 uniques categories.


In [20]:
# one hot encoding
sf_onehot = pd.get_dummies(sf_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
sf_onehot['Neighborhood'] = sf_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [sf_onehot.columns[-1]] + list(sf_onehot.columns[:-1])
sf_onehot = sf_onehot[fixed_columns]

sf_onehot.head()

Neighborhood  American Restaurant  Art Gallery  Art Museum  \
0      BAYVIEW                    0            0           0   
1      BAYVIEW                    0            0           0   
2      CENTRAL                    0            0           0   
3      CENTRAL                    0            0           0   
4      CENTRAL                    0            0           0   

   Arts & Crafts Store  Asian Restaurant  Athletics & Sports  Automotive Shop  \
0                    0                 0                   0                0   
1                    0                 0                   0                0   
2                    0                 0                   0                0   
3                    0                 0                   0                0   
4                    0                 0                   0                0   

   BBQ Joint  Bagel Shop  ...  Tourist Information Center  Trail  \
0          0           0  ...                           0      0   
1          0           0  ...                           0      0   
2          0           0  ...                           0      0   
3          0           0  ...                           0      0   
4          0           0  ...                           0      0   

   Vegetarian / Vegan Restaurant  Vietnamese Restaurant  Vineyard  Wine Bar  \
0                              0                      0         0         0   
1                              0                      0         0         0   
2                              0                      0         0         0   
3                              0                      0         0         0   
4                              0                      0         0         0   

   Wine Shop  Winery  Wings Joint  Yoga Studio  
0          0       0            0            0  
1          0       0            0            0  
2          0       0            0            0  
3          0       0            0            0  
4          0       0            0            0  

[5 rows x 177 columns]

In [21]:
sf_onehot.shape

(528, 177)

In [22]:
sf_grouped = sf_onehot.groupby('Neighborhood').mean().reset_index()
sf_grouped


Neighborhood  American Restaurant  Art Gallery  Art Museum  \
0      BAYVIEW             0.000000     0.000000    0.000000   
1      CENTRAL             0.000000     0.000000    0.000000   
2    INGLESIDE             0.000000     0.000000    0.000000   
3      MISSION             0.015152     0.075758    0.000000   
4     NORTHERN             0.000000     0.000000    0.000000   
5         PARK             0.000000     0.028986    0.014493   
6     RICHMOND             0.000000     0.000000    0.000000   
7     SOUTHERN             0.025000     0.012500    0.012500   
8      TARAVAL             0.027778     0.000000    0.000000   
9   TENDERLOIN             0.030000     0.040000    0.000000   

   Arts & Crafts Store  Asian Restaurant  Athletics & Sports  Automotive Shop  \
0             0.000000          0.000000            0.000000             0.00   
1             0.000000          0.000000            0.000000             0.00   
2             0.000000          0.047619            0.000000             0.00   
3             0.030303          0.015152            0.000000             0.00   
4             0.000000          0.000000            0.000000             0.00   
5             0.000000          0.000000            0.014493             0.00   
6             0.000000          0.010000            0.000000             0.01   
7             0.000000          0.000000            0.000000             0.00   
8             0.000000          0.000000            0.000000             0.00   
9             0.010000          0.000000            0.000000             0.00   

   BBQ Joint  Bagel Shop  ...  Tourist Information Center     Trail  \
0   0.000000      0.0000  ...                    0.000000  0.000000   
1   0.000000      0.0000  ...                    0.000000  0.000000   
2   0.000000      0.0000  ...                    0.000000  0.000000   
3   0.000000      0.0000  ...                    0.000000  0.000000   
4   0.000000      0.0000  ...                    0.000000  0.000000   
5   0.014493      0.0000  ...                    0.014493  0.014493   
6   0.020000      0.0000  ...                    0.000000  0.000000   
7   0.000000      0.0125  ...                    0.000000  0.000000   
8   0.000000      0.0000  ...                    0.000000  0.000000   
9   0.000000      0.0000  ...                    0.000000  0.000000   

   Vegetarian / Vegan Restaurant  Vietnamese Restaurant  Vineyard  Wine Bar  \
0                           0.00               0.000000    0.0000     0.000   
1                           0.00               0.000000    0.0000     0.000   
2                           0.00               0.047619    0.0000     0.000   
3                           0.00               0.015152    0.0000     0.000   
4                           0.00               0.000000    0.0000     0.000   
5                           0.00               0.000000    0.0000     0.000   
6                           0.00               0.030000    0.0000     0.000   
7                           0.00               0.000000    0.0125     0.025   
8                           0.00               0.027778    0.0000     0.000   
9                           0.01               0.040000    0.0000     0.010   

   Wine Shop    Winery  Wings Joint  Yoga Studio  
0   0.000000  0.000000     0.000000     0.000000  
1   0.000000  0.000000     0.037037     0.000000  
2   0.000000  0.000000     0.000000     0.000000  
3   0.000000  0.000000     0.000000     0.015152  
4   0.000000  0.000000     0.037037     0.000000  
5   0.000000  0.014493     0.000000     0.000000  
6   0.010000  0.000000     0.000000     0.000000  
7   0.000000  0.000000     0.000000     0.000000  
8   0.027778  0.000000     0.000000     0.000000  
9   0.010000  0.000000     0.000000     0.000000  

[10 rows x 177 columns]

In [23]:
sf_grouped.shape

(10, 177)

In [24]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [25]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = sf_grouped['Neighborhood']

for ind in np.arange(sf_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(sf_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0      BAYVIEW                   Gym                  Park   
1      CENTRAL                  Café                  Park   
2    INGLESIDE           Pizza Place            Poke Place   
3      MISSION           Art Gallery                  Café   
4     NORTHERN                  Café                  Park   

     3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0              Yoga Studio          Dessert Shop  Fast Food Restaurant   
1                 Dive Bar           Record Shop      Sushi Restaurant   
2             Dessert Shop       Bubble Tea Shop          Burger Joint   
3  New American Restaurant   Arts & Crafts Store                Bakery   
4                 Dive Bar           Record Shop      Sushi Restaurant   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0  Ethiopian Restaurant            Donut Shop               Dog Run   
1   Japanese Restaurant               Dog Run        Breakfast Spot   
2  Pakistani Restaurant          Liquor Store    Light Rail Station   
3  Gym / Fitness Center           Music Venue    Italian Restaurant   
4   Japanese Restaurant               Dog Run        Breakfast Spot   

  9th Most Common Venue 10th Most Common Venue  
0             Dive Shop               Dive Bar  
1           Roller Rink            Bus Station  
2           Bus Station               Bus Stop  
3          Cocktail Bar            Yoga Studio  
4           Roller Rink            Bus Station

In [26]:
# set number of clusters
kclusters = 5

sf_grouped_clustering = sf_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(sf_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([1, 4, 0, 2, 4, 2, 2, 2, 3, 2])

In [27]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

sf_merged = df_sf

# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
sf_merged = sf_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

sf_merged.head() # check the last columns!

Neighborhood  Count        lat         lng  Cluster Labels  \
0      BAYVIEW  14303  37.730400 -122.384400               1   
1      CENTRAL  17666  37.773972 -122.431297               4   
2    INGLESIDE  11594  37.719800 -122.453800               0   
3      MISSION  19503  37.759900 -122.414800               2   
4     NORTHERN  20100  37.773972 -122.431297               4   

  1st Most Common Venue 2nd Most Common Venue    3rd Most Common Venue  \
0                   Gym                  Park              Yoga Studio   
1                  Café                  Park                 Dive Bar   
2           Pizza Place            Poke Place             Dessert Shop   
3           Art Gallery                  Café  New American Restaurant   
4                  Café                  Park                 Dive Bar   

  4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
0          Dessert Shop  Fast Food Restaurant  Ethiopian Restaurant   
1           Record Shop      Sushi Restaurant   Japanese Restaurant   
2       Bubble Tea Shop          Burger Joint  Pakistani Restaurant   
3   Arts & Crafts Store                Bakery  Gym / Fitness Center   
4           Record Shop      Sushi Restaurant   Japanese Restaurant   

  7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
0            Donut Shop               Dog Run             Dive Shop   
1               Dog Run        Breakfast Spot           Roller Rink   
2          Liquor Store    Light Rail Station           Bus Station   
3           Music Venue    Italian Restaurant          Cocktail Bar   
4               Dog Run        Breakfast Spot           Roller Rink   

  10th Most Common Venue  
0               Dive Bar  
1            Bus Station  
2               Bus Stop  
3            Yoga Studio  
4            Bus Station

In [28]:
sf_tempm=sf_map

In [29]:
# add markers to the map
for lat, lon, poi, cluster in zip(sf_merged['lat'], sf_merged['lng'], sf_merged['Neighborhood'], sf_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=20,
        popup=label
        ).add_to(sf_tempm)
       
sf_tempm

<h4>THE LIGHT BLUE CIRCLES ARE THE HOTSPOTS THESE ARE THE CLUSTER OF AMENITIES<H4>
    


In [30]:
RADIUS_m=5000
#for fetching local transport like bus and metro stop
url = 'https://api.foursquare.com/v2/venues/search?client_id={}&client_secret={}&ll={},{},&query=MUNI&v=20200419&limit=100&radius={}'.format(
    CLIENT_ID,
    CLIENT_SECRET,
    37.773972,
    -122.431297,
    RADIUS_m)

In [31]:
result_m = requests.get(url).json()
result_m

{'meta': {'code': 200, 'requestId': '5e9c85afaba297001bab782b'},
 'response': {'venues': [{'id': '55d4db74498e6941d125d246',
    'name': 'SF MUNI - 5 (Outbound)',
    'location': {'lat': 37.779921021406295,
     'lng': -122.42920325044395,
     'labeledLatLngs': [{'label': 'display',
       'lat': 37.779921021406295,
       'lng': -122.42920325044395}],
     'distance': 687,
     'cc': 'US',
     'city': 'San Francisco',
     'state': 'CA',
     'country': 'United States',
     'formattedAddress': ['San Francisco, CA', 'United States']},
    'categories': [{'id': '4bf58dd8d48988d12b951735',
      'name': 'Bus Line',
      'pluralName': 'Bus Lines',
      'shortName': 'Bus',
      'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/travel/busstation_',
       'suffix': '.png'},
      'primary': True}],
    'referralId': 'v-1587316521',
    'hasPerk': False},
   {'id': '50e6140ce4b01130ad775e33',
    'name': 'MUNI Bus Stop - Fillmore & Oak',
    'location': {'address': 'Fillmore S

In [32]:
#making metro df
met =result_m['response']['venues']
metro=pd.json_normalize(met)
metro

id  \
0   55d4db74498e6941d125d246   
1   50e6140ce4b01130ad775e33   
2   4a0241edf964a52041711fe3   
3   4c81302ad92ea093fe7d3e72   
4   4c367a2fdfb0e21efb37aba8   
5   52310eea11d2cb66d5de5427   
6   49f3b8c4f964a520d56a1fe3   
7   4acbebcaf964a52056c820e3   
8   4a80dfdbf964a5205ff61fe3   
9   507dc6dae4b0e49c61999928   
10  4a3b19c3f964a52090a01fe3   
11  4f77a7efe4b01af713247d6b   
12  4d45e1e414aa8cfa2025773d   
13  4c925da42626a1cda10d3a6b   
14  4cd84785a423a35dd304eb42   
15  44f9c96ef964a5206e381fe3   
16  51118309e4b06e49557574dc   
17  4e1487547d8b4c0d630f4abd   
18  4f448628e4b00b32dfb5ecbc   
19  4c5dc94b6147be9a621c9309   
20  4c90107eb6d1a1430ebdc00f   
21  4eab99c730f823f86e60c52f   
22  4bbe874d85fbb713e9fd7067   
23  4bdaec93c79cc9284a4180e9   
24  4c4a624cbad7a593ef3249aa   
25  4f932b19e4b0c98ce0785bab   
26  4e8fbba4775bfdaabc0e9c16   
27  506e8e3ae4b08666bbde5498   
28  4ea7ac0b8b8154b19fc4834d   
29  4d8acbad401a224bd305aa18   
30  4ec5bc98cc21b428e102d479   
31  4b900ac4f964a520ff7133e3   
32  4e81eb390aaf4e1e90c33952   
33  4dff566552b1d747f679466c   
34  50776963e4b08ed6465f8cf3   
35  4e90adaad3e3187fc3050130   
36  5234a6c0498e983bfda5b4e9   
37  5c4666be35f983002c5aebd0   
38  4f34c699e4b0b9c46479e897   
39  4fe2da6be4b02bc55250f903   
40  4e9609768b811f0c661a6c9b   
41  4e8dcd31e5fa18aa8d41245b   
42  4dc8d7da1838e695fbdbcf32   
43  4f3b0722e4b03c8a49213283   
44  5111938ae4b09fcaa8d40113   
45  4bcb266dcc8cd13ababcbecf   
46  4fb26958e4b02fcbfcc38611   
47  4eda9a29b8f7fcd0408fc4f0   
48  58b5980799584241a54a4006   
49  50aaf8bfe4b03f0deaa837c4   

                                                 name  \
0                              SF MUNI - 5 (Outbound)   
1                      MUNI Bus Stop - Fillmore & Oak   
2                   MUNI Metro Stop - Duboce & Church   
3                                        MUNI N-Judah   
4                  MUNI Bus Stop - Hayes & Divisadero   
5   MUNI Stop ID #14618 Fillmore & Haight OUTBOUND 22   
6                         Van Ness MUNI Metro Station   
7                                  SF MUNI - 5 Fulton   
8                                  SF MUNI - 21 Hayes   
9                     MUNI Bus Stop - Castro & Duboce   
10                          Church MUNI Metro Station   
11              MUNI Bus Stop - Fillmore & McAllister   
12                                      MUNI Bus 5430   
13                                 MUNI J-Church Line   
14                  MUNI Bus Stop - Haight & Fillmore   
15                          Castro MUNI Metro Station   
16                     MUNI Bus Stop - Haight & Baker   
17         Muni 21 bus stop Hayes & Steiner - Inbound   
18                    MUNI Bus Stop - Haight & Pierce   
19                     MUNI Metro Stop - Duboce & Noe   
20                MUNI Bus Stop - California & Pierce   
21                                      MUNI bus 5489   
22                    MUNI Bus Stop - Haight & Pierce   
23        MUNI Metro Stop - Sunset Tunnel East Portal   
24                         MUNI Bus Stop - 14th & Noe   
25                   MUNI Bus Stop - Fillmore & Grove   
26                                      MUNI bus 5454   
27                MUNI Bus Stop - Divisadero & Sutter   
28                                      MUNI bus 5475   
29                MUNI Bus Stop - Haight & Divisadero   
30                 MUNI Bus Stop - Hermann & Fillmore   
31                     Muni Bus Stop - Laguna & Hayes   
32                 MUNI Bus Stop - Geary & Divisadero   
33                  MUNI Bus Stop - Haight & Buchanan   
34                                      MUNI bus 8135   
35                                      MUNI bus 5469   
36                    MUNI Bus Stop - Haight & Laguna   
37  MUNI Bus Stop #14005 - 22 OUTBOUND Church at D...   
38                                      MUNI bus 5472   
39                    MUNI Bus Stop - Church & Duboce   
40                    MUNI Bus Stop - Geary & Masonic   

In [33]:
filtered_columns = ['name', 'location.lat', 'location.lng']
metro =metro.loc[:, filtered_columns]
# clean columns

metro.columns = [col.split(".")[-1] for col in metro.columns]
metro


name        lat         lng
0                              SF MUNI - 5 (Outbound)  37.779921 -122.429203
1                      MUNI Bus Stop - Fillmore & Oak  37.774217 -122.430943
2                   MUNI Metro Stop - Duboce & Church  37.769451 -122.429528
3                                        MUNI N-Judah  37.769315 -122.433340
4                  MUNI Bus Stop - Hayes & Divisadero  37.774976 -122.437746
5   MUNI Stop ID #14618 Fillmore & Haight OUTBOUND 22  37.774031 -122.430871
6                         Van Ness MUNI Metro Station  37.775300 -122.419171
7                                  SF MUNI - 5 Fulton  37.778639 -122.431603
8                                  SF MUNI - 21 Hayes  37.775896 -122.431216
9                     MUNI Bus Stop - Castro & Duboce  37.768918 -122.435872
10                          Church MUNI Metro Station  37.767442 -122.429193
11              MUNI Bus Stop - Fillmore & McAllister  37.778512 -122.431836
12                                      MUNI Bus 5430  37.772140 -122.431930
13                                 MUNI J-Church Line  37.769345 -122.429111
14                  MUNI Bus Stop - Haight & Fillmore  37.772076 -122.430737
15                          Castro MUNI Metro Station  37.762380 -122.435429
16                     MUNI Bus Stop - Haight & Baker  37.770830 -122.440080
17         Muni 21 bus stop Hayes & Steiner - Inbound  37.775716 -122.432709
18                    MUNI Bus Stop - Haight & Pierce  37.771741 -122.433539
19                     MUNI Metro Stop - Duboce & Noe  37.769276 -122.433495
20                MUNI Bus Stop - California & Pierce  37.788576 -122.437175
21                                      MUNI bus 5489  37.771381 -122.430315
22                    MUNI Bus Stop - Haight & Pierce  37.771709 -122.433759
23        MUNI Metro Stop - Sunset Tunnel East Portal  37.769302 -122.433568
24                         MUNI Bus Stop - 14th & Noe  37.767477 -122.433369
25                   MUNI Bus Stop - Fillmore & Grove  37.776976 -122.431150
26                                      MUNI bus 5454  37.772580 -122.427445
27                MUNI Bus Stop - Divisadero & Sutter  37.785209 -122.439732
28                                      MUNI bus 5475  37.770829 -122.438637
29                MUNI Bus Stop - Haight & Divisadero  37.771317 -122.437144
30                 MUNI Bus Stop - Hermann & Fillmore  37.770292 -122.429959
31                     Muni Bus Stop - Laguna & Hayes  37.776667 -122.426239
32                 MUNI Bus Stop - Geary & Divisadero  37.783159 -122.439574
33                  MUNI Bus Stop - Haight & Buchanan  37.772761 -122.425874
34                                      MUNI bus 8135  37.772650 -122.426189
35                                      MUNI bus 5469  37.770782 -122.435391
36                    MUNI Bus Stop - Haight & Laguna  37.772750 -122.425504
37  MUNI Bus Stop #14005 - 22 OUTBOUND Church at D...  37.769629 -122.429276
38                                      MUNI bus 5472  37.770255 -122.427915
39                    MUNI Bus Stop - Church & Duboce  37.769454 -122.429518
40                    MUNI Bus Stop - Geary & Masonic  37.782572 -122.446406
41                   MUNI Bus Stop - Divisadero & Oak  37.772838 -122.437292
42                                      Muni Bus 5419  37.771310 -122.436973
43                                            Muni 21  37.776566 -122.426154
44                      MUNI Bus Stop - Hayes & Baker  37.774698 -122.441456
45                      MUNI Bus Stop - 18th & Castro  37.760907 -122.435251
46                     MUNI Bus Stop - Geary & Laguna  37.784901 -122.428185
47                    MUNI Bus Stop - Market & Church  37.767483 -122.429004
48                    MUNI Metro Stop - Church & 18th  37.760875 -122.428107
49                      MUNI Bus Stop - 14th & Church  37.767664 -122.429219

In [34]:
#adding the transport to the map
for lat, lng, label in zip(metro.lat, metro.lng, metro.name):
    folium.CircleMarker(
        [lat, lng],
        radius=1,
        color='red',
        popup=label,
        fill = True,
        fill_color='red',
        fill_opacity=0.6
    ).add_to(sf_map)
sf_map

<h4>THE RED MARKERS ARE PUBLIC TRANSPORTATION SPOTS</h4>




<h4>IF ANYONE WAS WONDERING WHY ALL HOTELS ARE IN A SINGLE PLACE THAT IS BECAUSE MOST HOTELS ARE LOCATED IN THAT PLACE<h4>

<H4>AFTER MAKING AN EDUCATED DECISION ON THE HOTEL TO CHOOSE</H4>
<H4>DECISION ON WHICH TRENDY PLACE TO VISIT CAN BE MADE
    
    
    
    

In [35]:
hot_nm=str(input("CHOOSE YOUR HOTEL FROM THE MAP AND COPY THE POP UP TEXT"))
select_h=hotels[hotels['name']==hot_nm].values
sh_lat=select_h[0,2]
sh_lng=select_h[0,3]
print("YOUR HOTEL",hot_nm,"LATITUDE IS: ",sh_lat)
print("YOUR HOTEL",hot_nm,"LONGITUDE IS:",sh_lng)

CHOOSE YOUR HOTEL FROM THE MAP AND COPY THE POP UP TEXTEdwardian San Francisco Hotel
YOUR HOTEL Edwardian San Francisco Hotel LATITUDE IS:  37.773455267551334
YOUR HOTEL Edwardian San Francisco Hotel LONGITUDE IS: -122.42159444218512


In [36]:
#getting trendy places
RADIUS_t=100000
url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&radius={}&limit=100&ll={},{}&section=sights'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    RADIUS_t,
    37.769722,
    -122.476944
    )

In [37]:
result_t = requests.get(url).json()
result_t

{'meta': {'code': 200, 'requestId': '5e9c863b71c428001b50328f'},
 'response': {'suggestedFilters': {'header': 'Tap to show:',
   'filters': [{'name': '$-$$$$', 'key': 'price'},
    {'name': 'Open now', 'key': 'openNow'}]},
  'headerLocation': 'San Francisco',
  'headerFullLocation': 'San Francisco',
  'headerLocationGranularity': 'city',
  'totalResults': 239,
  'suggestedBounds': {'ne': {'lat': 38.6697229000009,
    'lng': -121.34051819957432},
   'sw': {'lat': 36.869721099999104, 'lng': -123.61336980042569}},
  'groups': [{'type': 'Recommended Places',
    'name': 'recommended',
    'items': [{'reasons': {'count': 0,
       'items': [{'summary': 'This spot is popular',
         'type': 'general',
         'reasonName': 'globalInteractionReason'}]},
      'venue': {'id': '445e36bff964a520fb321fe3',
       'name': 'Golden Gate Park',
       'location': {'address': '501 Stanyan St',
        'crossStreet': 'btwn Fulton St & Lincoln Way',
        'lat': 37.76973638665379,
        'lng': -

In [38]:
venues = result_t['response']['groups'][0]['items']
    
nearby_venues = pd.io.json.json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues.head()

c:\users\aditya\appdata\local\programs\python\python37-32\lib\site-packages\ipykernel_launcher.py:3: FutureWarning: pandas.io.json.json_normalize is deprecated, use pandas.json_normalize instead
  This is separate from the ipykernel package so we can avoid doing imports until


name      categories        lat         lng
0                Golden Gate Park            Park  37.769736 -122.482049
1                Huntington Falls       Waterfall  37.768830 -122.473716
2                  Hellman Hollow            Park  37.769137 -122.485092
3  California Academy of Sciences  Science Museum  37.769841 -122.466349
4                       Stow Lake            Lake  37.769530 -122.474844

In [39]:
#creating a new map for sight seeing recommendations
sf_trendy= folium.Map(location=[37.773972, -122.431297], zoom_start=13)
sf_trendy.choropleth(
    geo_data=gjson,
    data=df_sf,
    columns=['Neighborhood','Count'],
    key_on='feature.properties.DISTRICT',
    fill_color='YlOrRd', 
    fill_opacity=0.7, 
    line_opacity=0.2,
    legend_name='San Francisco Crimes'
)
for lat, lng, label in zip(nearby_venues.lat, nearby_venues.lng, nearby_venues.name):
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        color='teal',
        popup=label,
        fill = True,
        fill_color='teal',
        fill_opacity=0.6
    ).add_to(sf_trendy)
sf_trendy

c:\users\aditya\appdata\local\programs\python\python37-32\lib\site-packages\folium\folium.py:415: FutureWarning: The choropleth  method has been deprecated. Instead use the new Choropleth class, which has the same arguments. See the example notebook 'GeoJSON_and_choropleth' for how to do this.
  FutureWarning


<h4>TOTAL OF 150 TRENDING PLACES IS DISPLAYED</h4>
<h4>CHOOSE A PLACE COPY THE POP UP AND PASTE IN THE DIALOG BOX AFTER EXECUTING THE BLOCK BELOW</h4>

In [40]:
tre_nm=input("SELECT A PLACE FROM ABOVE AND PASTE")
select_t=nearby_venues[nearby_venues['name']==tre_nm].values
st_lat=select_t[0,2]
st_lng=select_t[0,3]
print("YOUR PLACE",tre_nm,"LATITUDE IS: ",st_lat)
print("YOUR PLACE",tre_nm,"LONGITUDE IS:",st_lng)

SELECT A PLACE FROM ABOVE AND PASTEAsian Art Museum
YOUR PLACE Asian Art Museum LATITUDE IS:  37.780177691822274
YOUR PLACE Asian Art Museum LONGITUDE IS: -122.41650543857212


In [41]:
#getting police station near location
RADIUS_p=2000
url = 'https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&ll={},{},&query=police&v=20200419&limit=5&radius={}'.format(
    CLIENT_ID,
    CLIENT_SECRET,
    st_lat,
    st_lng,
    RADIUS_p)

In [42]:
result_pol = requests.get(url).json()
result_pol

{'meta': {'code': 200, 'requestId': '5e9c8709ad1ab40028f030b2'},
 'response': {'suggestedFilters': {'header': 'Tap to show:',
   'filters': [{'name': 'Open now', 'key': 'openNow'}]},
  'headerLocation': 'Civic Center',
  'headerFullLocation': 'Civic Center, San Francisco',
  'headerLocationGranularity': 'neighborhood',
  'query': 'police',
  'totalResults': 22,
  'suggestedBounds': {'ne': {'lat': 37.79817770982229,
    'lng': -122.39377370799915},
   'sw': {'lat': 37.76217767382226, 'lng': -122.43923716914509}},
  'groups': [{'type': 'Recommended Places',
    'name': 'recommended',
    'items': [{'reasons': {'count': 0,
       'items': [{'summary': 'This spot is popular',
         'type': 'general',
         'reasonName': 'globalInteractionReason'}]},
      'venue': {'id': '4b43f6acf964a52028ef25e3',
       'name': 'Tenderloin Police Station',
       'location': {'address': '301 Eddy St',
        'crossStreet': 'at Jones',
        'lat': 37.78382621650408,
        'lng': -122.412930919

In [43]:
pol = result_pol['response']['groups'][0]['items']
    
nearby_pol = pd.io.json.json_normalize(pol) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_pol =nearby_pol.loc[:, filtered_columns]

# filter the category for each row
nearby_pol['venue.categories'] = nearby_pol.apply(get_category_type, axis=1)

# clean columns
nearby_pol.columns = [col.split(".")[-1] for col in nearby_pol.columns]

nearby_pol

c:\users\aditya\appdata\local\programs\python\python37-32\lib\site-packages\ipykernel_launcher.py:3: FutureWarning: pandas.io.json.json_normalize is deprecated, use pandas.json_normalize instead
  This is separate from the ipykernel package so we can avoid doing imports until


name      categories        lat         lng
0           Tenderloin Police Station  Police Station  37.783826 -122.412931
1    SFPD Legal Division Court Liason  Police Station  37.775951 -122.404912
2           California Highway Patrol  Police Station  37.773013 -122.407297
3  San Francisco Sheriff's Department  Police Station  37.774924 -122.405210
4     San Francisco Police Department  Police Station  37.775112 -122.404934

In [44]:
#geting safe location
url = 'https://api.foursquare.com/v2/venues/search?client_id={}&client_secret={}&ll={},{},&query=starbucks&v=20200419&limit=5&radius={}'.format(
    CLIENT_ID,
    CLIENT_SECRET,
    st_lat,
    st_lng,
    RADIUS_p)

In [45]:
result_s = requests.get(url).json()
result_s

{'meta': {'code': 200, 'requestId': '5e9c877c47b43d0023384b7f'},
 'response': {'venues': [{'id': '49bee717f964a520f3541fe3',
    'name': 'Starbucks',
    'location': {'address': '1390 Market St',
     'crossStreet': 'at Fox Plz',
     'lat': 37.77708998,
     'lng': -122.4172976,
     'labeledLatLngs': [{'label': 'display',
       'lat': 37.77708998,
       'lng': -122.4172976},
      {'label': 'entrance', 'lat': 37.777193, 'lng': -122.417105}],
     'distance': 350,
     'postalCode': '94102',
     'cc': 'US',
     'city': 'San Francisco',
     'state': 'CA',
     'country': 'United States',
     'formattedAddress': ['1390 Market St (at Fox Plz)',
      'San Francisco, CA 94102',
      'United States']},
    'categories': [{'id': '4bf58dd8d48988d1e0931735',
      'name': 'Coffee Shop',
      'pluralName': 'Coffee Shops',
      'shortName': 'Coffee Shop',
      'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/food/coffeeshop_',
       'suffix': '.png'},
      'primary': True}

In [46]:
#cafes are open for a long time as well
#cafes are great places to seek help as they have wifi,staff can know multiple languages,and can are usually present in large no 
#the tourist can get food and drink to feel comforted 
star=result_s['response']['venues']
nearby_star=pd.json_normalize(star)
filtered_columns = ['name', 'location.lat', 'location.lng']
nearby_star =nearby_star.loc[:, filtered_columns]
nearby_star.columns = [col.split(".")[-1] for col in nearby_star.columns]
nearby_star

name        lat         lng
0  Starbucks  37.777090 -122.417298
1  Starbucks  37.784143 -122.407596
2  Starbucks  37.786170 -122.409060
3  Starbucks  37.788567 -122.422220
4  Starbucks  37.787122 -122.410674

In [47]:
sf_sel_trendy= folium.Map(location=[37.773972, -122.431297], zoom_start=13)
sf_sel_trendy.choropleth(
    geo_data=gjson,
    data=df_sf,
    columns=['Neighborhood','Count'],
    key_on='feature.properties.DISTRICT',
    fill_color='YlOrRd', 
    fill_opacity=0.7, 
    line_opacity=0.2,
    legend_name='San Francisco Crimes'
)

folium.Marker(   #location being visited
[st_lat,st_lng],
popop=tre_nm).add_to(sf_sel_trendy)


folium.Marker(     #hotel 
[sh_lat,sh_lng],
popop=hot_nm,
).add_to(sf_sel_trendy)

for lat, lng, label in zip(nearby_pol.lat, nearby_pol.lng, nearby_pol.name):    #police stations
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        color='navy',
        popup=label,
        fill = True,
        fill_color='blue',
        fill_opacity=0.6
    ).add_to(sf_sel_trendy)
sf_sel_trendy
for lat, lng, label in zip(nearby_star.lat, nearby_star.lng, nearby_star.name):   #safe locations
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        color='white',
        popup=label,
        fill = True,
        fill_color='green',
        fill_opacity=0.6
    ).add_to(sf_sel_trendy)
sf_sel_trendy

c:\users\aditya\appdata\local\programs\python\python37-32\lib\site-packages\folium\folium.py:415: FutureWarning: The choropleth  method has been deprecated. Instead use the new Choropleth class, which has the same arguments. See the example notebook 'GeoJSON_and_choropleth' for how to do this.
  FutureWarning


<h4> IN THIS MANNER A HOTEL CAN BE DECIDED AND THEN A PLACE TO VISIT CAN BE DECIDED AS WELL<h34>
    

<H4>SO TOURIST CAN HAVE A SAFE TRIP